# Grad-CAM Style Overlay (Image Processing)
This notebook produces **Grad-CAM-like** heatmaps with pure image processing (no deep learning). Use it to create red–blue overlays on target regions.

**Steps:**
1) Set `IMG_PATH`
2) (Optional) Set `ROI = (x1,y1,x2,y2)` to limit overlay
3) Run to save PNGs.

In [ ]:
# Image-Processing-Only Grad-CAM Style Overlay
# (No deep learning models required)

# If needed, install once:
# !pip install opencv-python numpy matplotlib

import cv2
import numpy as np
from pathlib import Path
import matplotlib.pyplot as plt

def load_rgb(path: str) -> np.ndarray:
    img_bgr = cv2.imread(path)
    if img_bgr is None:
        raise FileNotFoundError(f"Cannot read image: {path}")
    return cv2.cvtColor(img_bgr, cv2.COLOR_BGR2RGB)

def save_rgb(path: str, img_rgb: np.ndarray) -> str:
    path = str(path)
    img_bgr = cv2.cvtColor(img_rgb, cv2.COLOR_RGB2BGR)
    cv2.imwrite(path, img_bgr)
    return path

def normalize01(x: np.ndarray, eps: float = 1e-8) -> np.ndarray:
    x = x.astype(np.float32)
    mn, mx = x.min(), x.max()
    return (x - mn) / (mx - mn + eps)

def saliency_heatmap(img_rgb: np.ndarray, blur: int = 3) -> np.ndarray:
    """Create a Grad‑CAM‑style 'attention' map from pure image processing."""
    gray = cv2.cvtColor(img_rgb, cv2.COLOR_RGB2GRAY)
    sobelx = cv2.Sobel(gray, cv2.CV_32F, 1, 0, ksize=3)
    sobely = cv2.Sobel(gray, cv2.CV_32F, 0, 1, ksize=3)
    lap = cv2.Laplacian(gray, cv2.CV_32F, ksize=3)
    mag = np.sqrt(sobelx**2 + sobely**2) + 0.5 * np.abs(lap)
    heat = normalize01(mag)
    if blur and blur > 0:
        heat = cv2.GaussianBlur(heat, (blur|1, blur|1), 0)  # ensure odd kernel
    return heat

def overlay_heatmap(img_rgb: np.ndarray, heat: np.ndarray, alpha: float = 0.45,
                    colormap: int = cv2.COLORMAP_JET, roi_xyxy=None) -> np.ndarray:
    """Blend a color-mapped heatmap over the original image; optionally restrict to ROI=(x1,y1,x2,y2)."""
    h, w = img_rgb.shape[:2]
    heat = cv2.resize(heat, (w, h), interpolation=cv2.INTER_CUBIC)
    heat_uint8 = np.uint8(255 * normalize01(heat))
    heat_cm = cv2.applyColorMap(heat_uint8, colormap)
    heat_cm = cv2.cvtColor(heat_cm, cv2.COLOR_BGR2RGB)

    overlay = img_rgb.copy()
    if roi_xyxy is not None:
        x1, y1, x2, y2 = map(int, roi_xyxy)
        x1 = max(0, x1); y1 = max(0, y1)
        x2 = min(w, x2); y2 = min(h, y2)
        roi = overlay[y1:y2, x1:x2]
        roi_heat = heat_cm[y1:y2, x1:x2]
        blended = (roi * (1 - alpha) + roi_heat * alpha).astype(np.uint8)
        overlay[y1:y2, x1:x2] = blended
    else:
        overlay = (overlay * (1 - alpha) + heat_cm * alpha).astype(np.uint8)
    return overlay

def focus_lower_face_mask(img_rgb: np.ndarray, eye_y_ratio: float = 0.45) -> np.ndarray:
    """Soft mask focusing from ~eye level downward (lower face)."""
    h, w = img_rgb.shape[:2]
    y0 = int(h * eye_y_ratio)
    mask = np.zeros((h, w), dtype=np.float32)
    mask[y0:h, :] = 1.0
    edge = max(5, h // 50)
    if edge > 0:
        mask = cv2.GaussianBlur(mask, (edge|1, edge|1), 0)
        mask = normalize01(mask)
    return mask

def apply_masked_overlay(img_rgb: np.ndarray, overlay_rgb: np.ndarray, mask01: np.ndarray) -> np.ndarray:
    """Blend overlay only where mask is high (soft mask in [0,1])."""
    mask3 = np.dstack([mask01]*3)
    out = (img_rgb * (1 - mask3) + overlay_rgb * mask3).astype(np.uint8)
    return out

print("Loaded helper functions. Set IMG_PATH below and run the demo cell.")


## Run on your image

In [ ]:

# ==== Configure here ====
IMG_PATH = "YOUR_IMAGE.jpg"   # <-- replace with your image path
ROI = None                    # e.g., ROI = (120, 80, 360, 300)
OUT_DIR = Path("./ip_only_gradcam_outputs")
OUT_DIR.mkdir(parents=True, exist_ok=True)

# ==== Run ====<
img = load_rgb(IMG_PATH)
heat = saliency_heatmap(img, blur=9)

overlay_full = overlay_heatmap(img, heat, alpha=0.45, colormap=cv2.COLORMAP_JET, roi_xyxy=None)
overlay_roi  = overlay_heatmap(img, heat, alpha=0.45, colormap=cv2.COLORMAP_JET, roi_xyxy=ROI) if ROI else overlay_full

lower_mask = focus_lower_face_mask(img, eye_y_ratio=0.45)
overlay_for_mask = overlay_heatmap(img, heat, alpha=0.55, colormap=cv2.COLORMAP_JET, roi_xyxy=None)
masked = apply_masked_overlay(img, overlay_for_mask, lower_mask)

p1 = OUT_DIR / "overlay_full.png"
p2 = OUT_DIR / "overlay_roi.png"
p3 = OUT_DIR / "overlay_lower_face.png"

import matplotlib.pyplot as plt
plt.figure(); plt.imshow(overlay_full); plt.axis('off'); plt.title('Overlay (full)'); plt.savefig(p1, dpi=300, bbox_inches='tight'); plt.show()
plt.figure(); plt.imshow(overlay_roi); plt.axis('off'); plt.title('Overlay (ROI or full)'); plt.savefig(p2, dpi=300, bbox_inches='tight'); plt.show()
plt.figure(); plt.imshow(masked); plt.axis('off'); plt.title('Overlay (lower-face mask)'); plt.savefig(p3, dpi=300, bbox_inches='tight'); plt.show()

print("Saved:", p1, p2, p3)
